# Homework 5

The goal of Homework 5 is to get acquinted with the concepts of Ceteris Paribus and Partial Dependence Profiles. Ceteris Paribus Profile is a local explanation method, i.e. it operates on a single observation. It is based on a simple concept of computing the model's predictions when the values of all but one variable are fixed to constant values, and the single variable of interest takes values from a specific interval. Partial Dependence Profiles aim at creating a global explanation based on a set of Ceteris Paribus Profiles by averaging them over all available observations for each specific value of the variable of interest.

# Task 1

The aim of Task 1 is to calculate the PD profile for the $x_1$ variable of the following model:

$f(x_1, x_2) = (x_1 + x_2)^2$

where $x_1, x_2 \sim U[-1,1]$ and $x_1 = x_2$.

PD profile is in this case of the form:  

$\mathit{PD}_{x_1}(z) = E_{x_2}[f(x_{x_1 = z})]$

Therefore, we obtain the following:

$\mathit{PD}_{x_1}(z) = E_{x_2}[(x_1^2 + 2x_1x_2 + x_2^2)_{x_1 = z}] = \\
E_{x_2}[(x_1^2)_{x_1 = z}] + E_{x_2}[(2x_1x_2)_{x_1 = z}] + E_{x_2}[(x_2^2)_{x_1 = z}] = \\
z^2 + 0 + E_{x_2}[(x_2^2)_{x_1 = z}] =\\
z^2 + \frac{1}{3},$

where we have used the fact that

$E_{x_2}[x_2^2] = \int_{-1}^{1}x_2^2 \cdot \frac{1}{2}dx_2 = 2 \cdot \frac{1}{2}\int_0^1x_2^2dx_2 = [\frac{x_2^3}{3}]_0^1 = \frac{1}{3}.$

# Task 2

The aim of Task 2 is to see the aformentioned methods in practice. To follow up on the conclusions drawn from the previous homework, I will use the same dataset (*churn.csv*) and two previously explored models: random forest classifier (RF) and multilayer perceptron (MLP). These models are trained on $80\%$ of the entire dataset and evaluated on the other $20\%$. They achieve the following performance:

In [126]:
get_performance()

Model: random_forest
roc_auc: 0.770426225780277
pr_auc: 0.5140766975602556


Model: mlp
roc_auc: 0.7551437032596169
pr_auc: 0.4870963686232049




Importantly, these models achieve a very similar performance, with RF being slightly better than MLP. Therefore, explaining the inner workings of these models will allow us to decide which of them can be deployed safely.

We begin with an analysis of the RF model and its predictions for five randomly chosen observations shown below. Since the chosen dataset is highly imbalanced, it is not surprising that the predictions are very close to $0 - 0.1$ for four observations, and are slightly higher only for one observation which clearly stands out with its higher values of *total_day_minutes*, *total_day_charge* and *total_eve_minutes* values.

In [117]:
get_task_1()
x_test.iloc[:5, :]

Observation: 0, predicted probability: 0.09
Observation: 1, predicted probability: 0.01
Observation: 2, predicted probability: 0.03
Observation: 3, predicted probability: 0.02
Observation: 4, predicted probability: 0.37


total_day_minutes  total_day_charge  total_eve_minutes  \
2175              143.5             24.40              189.3   
2043              124.1             21.10              192.8   
591               125.7             21.37              207.6   
2148              144.0             24.48              224.7   
83                249.5             42.42              259.7   

      total_eve_charge  total_night_minutes  total_night_charge  \
2175             16.09                174.9                7.87   
2043             16.39                162.9                7.33   
591              17.65                183.1                8.24   
2148             19.10                227.7               10.25   
83               22.07                222.7               10.02   

      total_intl_minutes  total_intl_charge  
2175                 8.8               2.38  
2043                 6.4               1.73  
591                 12.9               3.48  
2148                10.0               2.70  
83                   9.8               2.65

We show the Ceteris Paribus Profiles for the RF model and these observations below. A clear pattern among low-probability observations is clearly observed - their profiles are typically very close to each other and behave in a similar manner. The *total_day_minutes*, as previous homeworks idnicate, once again seems to play the most important role as increasing it typically leads to a much higher predicted probability. The profiles for the *total_day_charge* variable show that it also plays an important and similar role. In terms of other variables, the profile for the high-probability observation seems to follow a slightly different pattern than the low-probability counterparts.

In [118]:
get_task_2()

Calculating ceteris paribus: 100%|██████████| 8/8 [00:00<00:00, 111.87it/s]


Next, our goal is to find two observations for which there exists a variable with profiles exhibiting two opposite behaviours. Finding such observations in the *churn* dataset is a pretty difficult task and there are no perfect candidates. The two presented below seem to be the best among many for the *total_day_minutes* variable - possibly the most important one. The profiles of these observations for this variable behave in a somewhat opposite way. Observation 2158 (higher probability) receives a decreasing probability when the *total_day_minutes* variable increases up to the point of around 200. At this point, it seems to slowly increase. Observation 591 (lower probability) seems to be almost insensitive to any changes in this variable up until 150 where it starts to achieve significantly higher probability. 

In [119]:
get_task_3()

Calculating ceteris paribus: 100%|██████████| 8/8 [00:00<00:00, 137.16it/s]


We proceed with an analysis of PD Profiles computed on the entire test set for the RF model. A higher curvature of a given profile indicates that the particular variable is of higher importance to the model. Clearly, and in line with previous findings, *total_day_minutes* seems to be the most important. Interestingly, the lowest probability appears at a point of 200 and grows in both directions but much more rapidly when this variable increases. The *total_day_charge* variable behaves very similarly. A conclusion could be drawn that a very high number of minutes spent using the phone characterizes the clients that churn. Interestingly, for both *total_intl_minutes* and *total_intl_charge*, the probability is almost insensitive to change up until a point where a sharp peak appears for higher values of these variables. This might also point to a characteristic of such clients.

In [120]:
get_task_4()

Calculating ceteris paribus: 100%|██████████| 8/8 [00:01<00:00,  6.96it/s]
/Users/bartlomiejsobieski/miniforge3/envs/mimuw_xai/lib/python3.10/site-packages/dalex/model_explanations/_aggregated_profiles/utils.py:144: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '[  0.      3.298   6.596 ... 323.204 326.502 329.8  ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.



At last, we compare the PD Profiles of the RF model with the ones of the MLP model. Unsurprisingly, the profiles of MLP are smooth, on the contrary to RF model. A very different behavior can be observed for *total_day_minutes* which, in this case, increases when the variable decreases. While *total_day_charge* profile is similar for higher values of this variable to the one of RF model, it decreases for lower values. Also, *total_intl_minutes* variable is used in the opposite way by MLP.

In [121]:
get_task_5()

Calculating ceteris paribus: 100%|██████████| 8/8 [00:00<00:00, 44.01it/s]
/Users/bartlomiejsobieski/miniforge3/envs/mimuw_xai/lib/python3.10/site-packages/dalex/model_explanations/_aggregated_profiles/utils.py:144: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '[  0.      3.298   6.596 ... 323.204 326.502 329.8  ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.



To summarize, Ceteris Paribus and Partial Dependence Profiles are simple explanation methods that provide an intuitive explanatory interface to the user. While they are rather ineffective in presenting complex relationships, there is still a lot of knowledge to gain about the model by inspecting them. Their simplicity allows for presenting such explanations even to non-specialists which is very important in practical scenarios.

# Appendix

In [48]:
import dalex as dx
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from sklearn.neural_network import MLPClassifier
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score, average_precision_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.pipeline import Pipeline

In [49]:
PATH_DATASET = 'churn.csv'
DATASET = pd.read_csv(PATH_DATASET, index_col = 0)

In [50]:
SEED = 0

In [51]:
METRICS = {
    'roc_auc': roc_auc_score,
    'pr_auc': average_precision_score}

In [52]:
MODELS = {
    'random_forest': RandomForestClassifier(random_state = SEED),
    'mlp': Pipeline([
        ('standard_scaler', StandardScaler()),
        ('mlp', MLPClassifier((32, 32), 'relu', random_state = SEED, max_iter = 1000))])}

In [53]:
def get_train_test_split():
    x, y = DATASET.iloc[:, :-1], DATASET.iloc[:, -1]
    return train_test_split(x, y)

def train_models():
    x_train, x_test, y_train, y_test = get_train_test_split()
    results = {model_name: {} for model_name in MODELS.keys()}
    trained_models = {}
    for model_name, model in MODELS.items():
        model.fit(x_train, y_train)
        trained_models[model_name] = model
        y_pred = model.predict_proba(x_test)[:, -1]
        for metric_name, metric in METRICS.items():
            results[model_name][metric_name] = metric(y_test, y_pred)
    print('Finished')
    return trained_models, results

In [54]:
trained_models, test_metrics = train_models()
x_train, x_test, y_train, y_test = get_train_test_split()

Finished


In [55]:
explainers = {}
for model_name, model in trained_models.items():
    explainers[model_name] = dx.Explainer(model, x_test, y_test, label = model_name)

Preparation of a new explainer is initiated

  -> data              : 1250 rows 8 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Converted to a numpy.ndarray.
  -> target variable   : 1250 values
  -> model_class       : sklearn.ensemble._forest.RandomForestClassifier (default)
  -> label             : random_forest
  -> predict function  : <function yhat_proba_default at 0x11e64d480> will be used (default)
  -> predict function  : Accepts pandas.DataFrame and numpy.ndarray.
  -> predicted values  : min = 0.0, mean = 0.133, max = 1.0
  -> model type        : classification will be used (default)
  -> residual function : difference between y and yhat (default)
  -> residuals         : min = -0.55, mean = -0.00601, max = 1.0
  -> model_info        : package sklearn

A new explainer has been created!
Preparation of a new explainer is initiated

  -> data              : 1250 rows 8 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Converted to a numpy.ndarr

/Users/bartlomiejsobieski/miniforge3/envs/mimuw_xai/lib/python3.10/site-packages/sklearn/base.py:465: UserWarning:

X does not have valid feature names, but RandomForestClassifier was fitted with feature names

/Users/bartlomiejsobieski/miniforge3/envs/mimuw_xai/lib/python3.10/site-packages/sklearn/base.py:465: UserWarning:

X does not have valid feature names, but StandardScaler was fitted with feature names



In [125]:
def get_performance():
    for model_name, metrics in test_metrics.items():
        print(f'Model: {model_name}')
        for metric_name, value in metrics.items():
            print(f'{metric_name}: {value}')
        print('\n')

get_performance()

Model: random_forest
roc_auc: 0.770426225780277
pr_auc: 0.5140766975602556


Model: mlp
roc_auc: 0.7551437032596169
pr_auc: 0.4870963686232049




In [65]:
x_test

total_day_minutes  total_day_charge  total_eve_minutes  \
2175              143.5             24.40              189.3   
2043              124.1             21.10              192.8   
591               125.7             21.37              207.6   
2148              144.0             24.48              224.7   
83                249.5             42.42              259.7   
...                 ...               ...                ...   
2191               90.6             15.40              170.6   
1105              201.4             34.24              246.5   
4043              214.0             36.38              245.3   
3385              172.2             29.27              161.6   
7                 157.0             26.69              103.1   

      total_eve_charge  total_night_minutes  total_night_charge  \
2175             16.09                174.9                7.87   
2043             16.39                162.9                7.33   
591              17.65                183.1                8.24   
2148             19.10                227.7               10.25   
83               22.07                222.7               10.02   
...                ...                  ...                 ...   
2191             14.50                137.4                6.18   
1105             20.95                154.8                6.97   
4043             20.85                205.6                9.25   
3385             13.74                259.7               11.69   
7                 8.76                211.8                9.53   

      total_intl_minutes  total_intl_charge  
2175                 8.8               2.38  
2043                 6.4               1.73  
591                 12.9               3.48  
2148                10.0               2.70  
83                   9.8               2.65  
...                  ...                ...  
2191                 5.4               1.46  
1105                12.9               3.48  
4043                10.3               2.78  
3385                11.8               3.19  
7                    7.1               1.92  

[1250 rows x 8 columns]

In [103]:
def get_task_1():
    obs = x_test.iloc[:5, :]
    model = trained_models['random_forest']
    preds = model.predict_proba(obs)[:, 1]
    [print(f'Observation: {obs_id}, predicted probability: {prob}') for obs_id, prob in enumerate(preds)]

get_task_1()
x_test.iloc[:5, :]

Observation: 0, predicted probability: 0.09
Observation: 1, predicted probability: 0.01
Observation: 2, predicted probability: 0.03
Observation: 3, predicted probability: 0.02
Observation: 4, predicted probability: 0.37


total_day_minutes  total_day_charge  total_eve_minutes  \
2175              143.5             24.40              189.3   
2043              124.1             21.10              192.8   
591               125.7             21.37              207.6   
2148              144.0             24.48              224.7   
83                249.5             42.42              259.7   

      total_eve_charge  total_night_minutes  total_night_charge  \
2175             16.09                174.9                7.87   
2043             16.39                162.9                7.33   
591              17.65                183.1                8.24   
2148             19.10                227.7               10.25   
83               22.07                222.7               10.02   

      total_intl_minutes  total_intl_charge  
2175                 8.8               2.38  
2043                 6.4               1.73  
591                 12.9               3.48  
2148                10.0               2.70  
83                   9.8               2.65

In [105]:
def get_task_2():
    obs = x_test.iloc[:5, :]
    explainers['random_forest'].predict_profile(obs).plot()

get_task_2()

Calculating ceteris paribus: 100%|██████████| 8/8 [00:00<00:00, 115.58it/s]


In [107]:
def get_task_3():
    ids = [591, 2158]
    obs = x_test.loc[ids, :]
    model = trained_models['random_forest']
    model.predict_proba(obs)[:, 1]
    explainers['random_forest'].predict_profile(obs).plot()

get_task_3()

Calculating ceteris paribus: 100%|██████████| 8/8 [00:00<00:00, 136.47it/s]


In [115]:
def get_task_4():
    explainers['random_forest'].model_profile().plot()

get_task_4()

Calculating ceteris paribus: 100%|██████████| 8/8 [00:01<00:00,  6.90it/s]
/Users/bartlomiejsobieski/miniforge3/envs/mimuw_xai/lib/python3.10/site-packages/dalex/model_explanations/_aggregated_profiles/utils.py:144: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '[  0.      3.298   6.596 ... 323.204 326.502 329.8  ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.



In [116]:
def get_task_5():
    explainers['mlp'].model_profile().plot()

get_task_5()

Calculating ceteris paribus: 100%|██████████| 8/8 [00:00<00:00, 48.63it/s]
/Users/bartlomiejsobieski/miniforge3/envs/mimuw_xai/lib/python3.10/site-packages/dalex/model_explanations/_aggregated_profiles/utils.py:144: FutureWarning:

Setting an item of incompatible dtype is deprecated and will raise in a future error of pandas. Value '[  0.      3.298   6.596 ... 323.204 326.502 329.8  ]' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.

